## Compare several "Composite" portfolio
### "Composite" portfolio : `[CorrClusterSelector, DualMomentumSelector, "Optimizer"]`
It is a `ModelPipeline` of 2 Selctors and 1 optimizer
where "Optimizer" are instances of `CVaRAnalyzer`, `KellyEngine`, "EWP", `SDAnalyzer`, `MADAnalyzer`, and `LSDAnalyzer`

In [27]:
import numpy as np
import pandas as pd

import sys
sys.path.append("..")
import azapy as az
print(f"azapy version {az.version()} >= 1.2.0", flush=True)

azapy version 1.2.2 >= 1.2.0


### Collect market data

In [28]:
mktdir = '../MkTdata'
sdate = '2012-01-01'
edate = 'today'

symb = ['GLD', 'TLT', 'IHI', 'VGT', 'OIH',
        'XAR', 'XBI', 'XHE', 'XHS', 'XLB',
        'XLE', 'XLF', 'XLI', 'XLK', 'XLU', 
        'XLV', 'XLY', 'XRT', 'SPY', 'ONEQ', 
        'QQQ', 'DIA', 'ILF', 'XSW', 'PGF', 
        'IDV', 'JNK', 'HYG', 'SDIV', 'VIG', 
        'SLV', 'AAPL', 'MSFT', 'AMZN', 'GOOG', 
        'IYT', 'VIG', 'IWM', 'BRK-B', 'ITA']

mktdata = az.readMkT(symb, sdate=sdate, edate=edate, file_dir=mktdir, 
                     verbose=False)

### Set general parameters for Selectors and Port_Generator

In [29]:
corr_threshold = 0.98
freq = 'Q'

nw = 5
ths = np.floor(len(symb) * 0.3)

hlength = 1.25
rtype = 'Sharpe'
mu0 = 0.01

histoffset = hlength
fixoffset = -1

### "Optimizer" = CVaRAnalyzer

In [30]:
pname = 'CVaR'
ccs = az.CorrClusterSelector(corr_threshold=corr_threshold, freq=freq)
dms = az.DualMomentumSelector(nw=nw, threshold=ths)
alpha = [0.95, 0.9]
cvar = az.CVaRAnalyzer(alpha=alpha, freq=freq, hlength=hlength,
                       rtype=rtype, mu0=mu0)
model = az.ModelPipeline([ccs, dms, cvar])
pp_cvar = az.Port_Generator(mktdata, 
                       freq=freq, 
                       fixoffset=fixoffset, 
                       histoffset=histoffset,
                       pname=pname)
port_cvar = pp_cvar.set_model(model)
_ = pp_cvar.port_view(fancy=True)

### "Optimizer" = KellyEngine

In [31]:
pname = 'Kelly'
ccs = az.CorrClusterSelector(corr_threshold=corr_threshold, freq=freq)
dms = az.DualMomentumSelector(nw=nw, threshold=ths)
kelly = az.KellyEngine(freq=freq, hlength=hlength)
model = az.ModelPipeline([ccs, dms, kelly])
pp_kelly = az.Port_Generator(mktdata, 
                             freq=freq, 
                             fixoffset=fixoffset, 
                             histoffset=histoffset,
                             pname=pname)
port_kelly = pp_kelly.set_model(model)
_ = pp_kelly.port_view(fancy=True)

### "Optimizer" = MADAnalyzer

In [32]:
pname = 'MAD'
ccs = az.CorrClusterSelector(corr_threshold=corr_threshold, freq=freq)
dms = az.DualMomentumSelector(nw=nw, threshold=ths)
coef = [1, 1, 1, 1]
mad = az.MADAnalyzer(coef=coef, freq=freq, hlength=hlength)
model = az.ModelPipeline([ccs, dms, mad])
pp_mad = az.Port_Generator(mktdata, 
                             freq=freq, 
                             fixoffset=fixoffset, 
                             histoffset=histoffset,
                             pname=pname)
port_mad = pp_mad.set_model(model)
_ = pp_mad.port_view(fancy=True)

### "Optimizer" = "EWP"

In [33]:
pname = 'EWP'
ccs = az.CorrClusterSelector(corr_threshold=corr_threshold, freq=freq)
nw_ewp = 3
dms = az.DualMomentumSelector(nw=nw_ewp, threshold=ths)
model = az.ModelPipeline([ccs, dms, "EWP"])
pp_ewp = az.Port_Generator(mktdata, 
                             freq=freq, 
                             fixoffset=fixoffset, 
                             histoffset=histoffset,
                             pname=pname)
port_ewp = pp_ewp.set_model(model)
_ = pp_ewp.port_view(fancy=True)

### "Optimizer" = SDAnalyzer

In [34]:
pname = 'SD'
ccs = az.CorrClusterSelector(corr_threshold=corr_threshold, freq=freq)
dms = az.DualMomentumSelector(nw=nw, threshold=ths)
sd = az.SDAnalyzer(freq=freq, hlength=hlength)
model = az.ModelPipeline([ccs, dms, sd])
pp_sd = az.Port_Generator(mktdata, 
                             freq=freq, 
                             fixoffset=fixoffset, 
                             histoffset=histoffset,
                             pname=pname)
port_sd = pp_sd.set_model(model)
_ = pp_sd.port_view(fancy=True)

### "Optimizer" = LSDAnalyzer

In [35]:
pname = 'LSD'
ccs = az.CorrClusterSelector(corr_threshold=corr_threshold, freq=freq)
dms = az.DualMomentumSelector(nw=nw, threshold=ths)
coef = [1, 1, 1, 1]
lsd = az.LSDAnalyzer(coef=coef, freq=freq, hlength=hlength)
model = az.ModelPipeline([ccs, dms, lsd])
pp_lsd = az.Port_Generator(mktdata, 
                             freq=freq, 
                             fixoffset=fixoffset, 
                             histoffset=histoffset,
                             pname=pname)
port_lsd = pp_lsd.set_model(model)
_ = pp_lsd.port_view(fancy=True)

### Compare the portfolio strategies

In [36]:
pq = az.Port_Simple([port_cvar, port_kelly, port_mad, port_ewp, port_sd, port_lsd])
_ = pq.set_model()
_ = pq.port_view_all(componly=True, fancy=True)

### Compare the overall performance of the strategies

In [37]:
pq.port_perf(componly=True, fancy=True)

RR     DD     RoMaD     DD_date    DD_start      DD_end
symbol                                                            
SD      16.88 -27.39  0.616250  2022-05-24  2022-03-29  2022-11-11
MAD     16.54 -28.16  0.587514  2022-05-24  2022-01-03  2023-01-23
CVaR    16.66 -30.85  0.540051  2022-05-24  2022-01-03  2023-02-02
LSD     16.42 -30.83  0.532604  2022-05-24  2022-01-03  2023-02-02
EWP     17.05 -36.51  0.466986  2020-10-28  2020-06-08  2023-01-26
Kelly   13.95 -35.71  0.390577  2022-05-24  2020-12-28  2023-03-20

### Compare annual returns 

In [38]:
an_cvar = pp_cvar.port_annual_returns()
an_kelly = pp_kelly.port_annual_returns()
an_ewp = pp_ewp.port_annual_returns()
an_sd = pp_sd.port_annual_returns()
an_mad = pp_mad.port_annual_returns()
an_lsd = pp_lsd.port_annual_returns()
(an_cvar.join(an_kelly).join(an_ewp).join(an_sd).join(an_mad).join(an_lsd) * 100).round(2)

CVaR  Kelly    EWP     SD    MAD    LSD
year                                          
2013  16.93  16.93  15.82  12.60  14.65  14.51
2014  -8.69 -21.21  -9.85  -7.01  -8.64  -8.73
2015  10.73  27.91   7.81  12.20  12.85  10.09
2016  26.49  24.43  46.54  24.78  24.92  26.14
2017  15.61  -1.50   5.67  15.66  15.09  15.91
2018  18.28  23.72  21.70  15.46  12.38  18.59
2019  21.60  21.60  17.52  21.62  21.60  21.60
2020  46.09  45.95  49.62  46.11  46.06  46.09
2021   5.82  -5.27  -2.09   6.18   6.24   6.23
2022 -11.22 -11.18   0.54  -6.48  -7.79 -11.20
2023  50.78  50.73  40.23  51.51  52.96  50.69

### Compare the rebalancing period returns

In [39]:
zz_cvar = pp_cvar.port_period_returns().drop('Dfix', axis=1).set_index('Droll')[['RR']].rename({'RR': pp_cvar.pname}, axis=1)
zz_kelly = pp_kelly.port_period_returns().drop('Dfix', axis=1).set_index('Droll')[['RR']].rename({'RR': pp_kelly.pname}, axis=1)
zz_ewp = pp_ewp.port_period_returns().drop('Dfix', axis=1).set_index('Droll')[['RR']].rename({'RR': pp_ewp.pname}, axis=1)
zz_sd = pp_sd.port_period_returns().drop('Dfix', axis=1).set_index('Droll')[['RR']].rename({'RR': pp_sd.pname}, axis=1)
zz_mad = pp_mad.port_period_returns().drop('Dfix', axis=1).set_index('Droll')[['RR']].rename({'RR': pp_mad.pname}, axis=1)
zz_lsd = pp_lsd.port_period_returns().drop('Dfix', axis=1).set_index('Droll')[['RR']].rename({'RR': pp_lsd.pname}, axis=1)
(zz_cvar.join(zz_kelly).join(zz_ewp).join(zz_sd).join(zz_mad).join(zz_lsd) * 100).round(2)

CVaR  Kelly    EWP     SD    MAD    LSD
Droll                                               
2013-06-25   9.42   9.42  13.74   9.42   9.42   9.42
2013-09-25   6.42   6.42   1.48   2.29   4.24   4.09
2013-12-26   2.37   2.37   0.90   2.56   2.47   2.48
2014-03-26   0.94   2.86   0.10   0.30   0.34   0.92
2014-06-25   1.70   1.76   1.30   1.71   1.70   1.70
2014-09-25 -13.15 -27.85 -13.13 -11.27 -12.66 -13.12
2014-12-26   2.47   4.39   3.11   2.78   2.55   2.42
2015-03-26   6.05  10.47   4.45   5.15   4.66   5.47
2015-06-25  -4.70   5.17   1.56  -3.02  -1.73  -4.82
2015-09-25   9.37   9.92   0.68   9.82   9.52   9.48
2015-12-28  -1.81  -1.82   5.23  -1.80  -1.80  -1.82
2016-03-28   2.29   2.26   2.35   2.27   2.24   2.25
2016-06-27  16.27  16.30  23.48  16.29  16.32  16.32
2016-09-27   6.95   6.32   8.57   5.12   5.30   6.63
2016-12-27   9.34  10.15  10.71   9.08   9.23   9.26
2017-03-28   2.30 -13.68  -6.91   2.11   1.47   2.07
2017-06-27   1.29   0.18   1.37   2.00   2.05   1.79
2017-09-26   2.26   2.42   1.33   2.41   2.28   2.33
2017-12-26  -1.67  -1.65  -0.81  -1.66  -1.65  -1.65
2018-03-26   5.04   9.87   4.08   5.20   5.48   5.07
2018-06-26  13.52  13.54   7.95   5.79   2.30   9.40
2018-09-25  -7.46  -7.50   2.34  -2.97  -2.58  -3.57
2018-12-26  28.64  28.67  30.85  28.33  28.31  28.41
2019-03-26  -3.54  -3.52  -6.74  -3.54  -3.54  -3.51
2019-06-25   4.28   4.25  -0.09   4.27   4.28   4.26
2019-09-25   2.64   2.63   4.74   2.63   2.63   2.63
2019-12-26  -0.08  -0.08   0.71  -0.05  -0.07  -0.09
2020-03-26  11.57  11.57  31.80  11.55  11.54  11.56
2020-06-25   6.79   6.79 -13.99   6.79   6.79   6.80
2020-09-25  25.58  25.58  28.79  25.57  25.60  25.57
2020-12-28  -3.88  -4.72   3.70  -3.73  -3.77  -3.80
2021-03-26   0.89   0.69   1.33   0.88   0.93   0.89
2021-06-25   0.14  -1.16  -1.36   0.22   0.18   0.16
2021-09-27   4.70  -1.85  -4.28   5.53   5.33   4.92
2021-12-28  -7.88  -9.89  -0.83  -2.91  -4.21  -7.84
2022-03-28 -17.72 -17.71 -10.67 -18.10 -17.97 -17.70
2022-06-27  -3.50  -3.50  -3.46  -3.50  -3.51  -3.66
2022-09-27  25.67  25.70  19.31  25.68  25.66  25.85
2022-12-27  19.67  19.69  15.29  19.68  19.67  19.70
2023-03-28   4.48   4.47   8.09   4.86   5.59   4.49
2023-06-27  -2.28  -2.32  -0.43  -2.24  -1.97  -2.41
2023-09-26  17.17  17.18  11.91  17.26  17.23  17.23